<a href="https://colab.research.google.com/github/InNoobWeTrust/made-up-noob-algo/blob/main/parallel_programming/parallel_programming_practice.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
'''
# Problem statement:
Given a sequence of numbers, find the missing numbers?

Example data: 1 2 3 5

Assumption:
- sorted
- incrementally
- data length n is a fixed constant
- fixed size, can be large (but manageable size)

Edge case:
- Array can start from any number
- No number overflow (int64)
'''

import random
import sys
import numpy as np

NUM_ITEMS = 10
def prepare_test_data(n = NUM_ITEMS, step = 1):
    '''
    TDD approach to problem: define test datasets first
    This kind of data is easy to augment
    '''
    if n == 1:
        n = NUM_ITEMS
    # randomly pick a start number
    rand_start = random.randint(0, sys.maxsize - n * step)
    arr = list(range(rand_start, rand_start + (n + 1) * step, step))
    # randomly remove a number in the middle
    rand_idx = random.choice(range(1, n))
    missing = arr.pop(rand_idx)
    return arr, missing

In [2]:
'''
Check the generated test data
'''
test_arr, missing_num = prepare_test_data(int(1e5), 5)
print('Test data:', test_arr)
print('Missing number:', missing_num)

Test data: [7871893230629454711, 7871893230629454716, 7871893230629454721, 7871893230629454726, 7871893230629454731, 7871893230629454736, 7871893230629454741, 7871893230629454746, 7871893230629454751, 7871893230629454756, 7871893230629454761, 7871893230629454766, 7871893230629454771, 7871893230629454776, 7871893230629454781, 7871893230629454786, 7871893230629454791, 7871893230629454796, 7871893230629454801, 7871893230629454806, 7871893230629454811, 7871893230629454816, 7871893230629454821, 7871893230629454826, 7871893230629454831, 7871893230629454836, 7871893230629454841, 7871893230629454846, 7871893230629454851, 7871893230629454856, 7871893230629454861, 7871893230629454866, 7871893230629454871, 7871893230629454876, 7871893230629454881, 7871893230629454886, 7871893230629454891, 7871893230629454896, 7871893230629454901, 7871893230629454906, 7871893230629454911, 7871893230629454916, 7871893230629454921, 7871893230629454926, 7871893230629454931, 7871893230629454936, 7871893230629454941, 7

In [3]:
'''
Intuition:
- We know the step size
- First and last number in an array is not the missing number
- If 2 consecutive numbers in the array is not increasing with the step
  size, then we have a missing number in between. Simple?
'''

def validate_increasing(a, b, step = 1):
    '''
    Simple logic to check if 2 consecutive numbers is increasing
    with given step size
    '''
    return b - step == a

def check_missing_number(arr, step = 1):
    '''
    Simple check logic on a stride of sliding window
    '''
    for i in range(0, len(arr) - 1):
        if not validate_increasing(arr[i], arr[i+1], step):
            return arr[i] + step
    return None

import os
from multiprocessing.pool import ThreadPool

def check_missing_parallel(arr, step = 1):
    '''
    - Split the data to multiple windows with overlap of 1 item.
    - Then for each window, let a thread/process do the job of
    finding the missing number. Then wait and collect results
    - Find a truthy value among the returned results
    '''
    num_proc = os.cpu_count() or 2
    window = len(arr) // num_proc
    splits = [arr[i : i + window + 1] for i in range(num_proc)]
    with ThreadPool(os.cpu_count()) as pool:
        candidates = pool.map(lambda w: check_missing_number(w, step), splits)
    return list(filter(None, candidates))[:1] or None

In [4]:
test_arr, missing_num = prepare_test_data(int(1e5), 5)
print('Test data:', test_arr)
print('Missing number:', missing_num)

Test data: [2884611469687383458, 2884611469687383463, 2884611469687383468, 2884611469687383473, 2884611469687383478, 2884611469687383483, 2884611469687383488, 2884611469687383493, 2884611469687383498, 2884611469687383503, 2884611469687383508, 2884611469687383513, 2884611469687383518, 2884611469687383523, 2884611469687383528, 2884611469687383533, 2884611469687383538, 2884611469687383543, 2884611469687383548, 2884611469687383553, 2884611469687383558, 2884611469687383563, 2884611469687383568, 2884611469687383573, 2884611469687383578, 2884611469687383583, 2884611469687383588, 2884611469687383593, 2884611469687383598, 2884611469687383603, 2884611469687383608, 2884611469687383613, 2884611469687383618, 2884611469687383623, 2884611469687383628, 2884611469687383633, 2884611469687383638, 2884611469687383643, 2884611469687383648, 2884611469687383653, 2884611469687383658, 2884611469687383663, 2884611469687383668, 2884611469687383673, 2884611469687383678, 2884611469687383683, 2884611469687383688, 2

In [5]:
%time
check_missing_number(test_arr, 5)

CPU times: user 4 µs, sys: 1e+03 ns, total: 5 µs
Wall time: 10 µs


2884611469687789968

In [6]:
%time
check_missing_parallel(test_arr, 5)

CPU times: user 4 µs, sys: 1e+03 ns, total: 5 µs
Wall time: 9.78 µs


In [7]:
test_arr, missing_num = prepare_test_data(100, 5)
print('Test data:', test_arr)
print('Missing number:', missing_num)

Test data: [5183170731453939086, 5183170731453939091, 5183170731453939096, 5183170731453939101, 5183170731453939106, 5183170731453939111, 5183170731453939116, 5183170731453939121, 5183170731453939126, 5183170731453939131, 5183170731453939136, 5183170731453939141, 5183170731453939146, 5183170731453939151, 5183170731453939156, 5183170731453939161, 5183170731453939166, 5183170731453939171, 5183170731453939176, 5183170731453939181, 5183170731453939186, 5183170731453939191, 5183170731453939196, 5183170731453939201, 5183170731453939206, 5183170731453939211, 5183170731453939216, 5183170731453939221, 5183170731453939226, 5183170731453939231, 5183170731453939236, 5183170731453939241, 5183170731453939246, 5183170731453939256, 5183170731453939261, 5183170731453939266, 5183170731453939271, 5183170731453939276, 5183170731453939281, 5183170731453939286, 5183170731453939291, 5183170731453939296, 5183170731453939301, 5183170731453939306, 5183170731453939311, 5183170731453939316, 5183170731453939321, 5

In [8]:
%time
check_missing_number(test_arr, 5)

CPU times: user 4 µs, sys: 1e+03 ns, total: 5 µs
Wall time: 8.11 µs


5183170731453939251

In [9]:
%time
check_missing_parallel(test_arr, 5)

CPU times: user 4 µs, sys: 0 ns, total: 4 µs
Wall time: 7.15 µs


[5183170731453939251]

# Conclusion
Not worth optimizing using parallel programming, just use a noob's version, easier to understand and easier to find bug.

Or if you want to do it anyway, combine parallel programming with recursive divide-and-conquer for the solution with highest complexity ever (and be aware of the stack-overflow issue on threads with limit stack size like on GPUs).

Until we see performance issue, then we fix...
Or simply say `It's not a bug, it's a feature!`